# Initialization

Default initialization as usual.

In [1]:
import sys
sys.path.append("wrappers")
from modelverse import *

init()
login("admin", "admin")

# New metamodel

Define a new metamodel by instantiation SimpleClassDiagrams.

In [2]:
model_add("formalisms/MyOwnFSA", "formalisms/SimpleClassDiagrams", "")

We can now easily add an instance model.

In [3]:
model_add("my_FSA", "formalisms/MyOwnFSA")

Nonetheless, we cannot instantiate any element in that model, as the metamodel is empty.

In [4]:
types("my_FSA")

set()

And indeed, instantiating a state yields an exception.

In [5]:
try:
    instantiate("my_FSA", "State")
except UnknownElement:
    print("Type State not defined!")

Type State not defined!


# Creating classes

A first step is to define some classes that we would like to use, such as states and transitions.
This is done as follows, similar to the usual model instantiation.

In [6]:
model_add("formalisms/MyOwnFSA", "formalisms/SimpleClassDiagrams", """
    Class State {
        name = "State"
    }

    Association Transition (State, State) {
        name = "Transition"
    }
    """)

This allows us to instantiate elements of these types.

In [7]:
types("my_FSA")

{('State', 'Class'),
 ('State.name', 'String'),
 ('Transition', 'Association'),
 ('Transition.name', 'String'),
 ('__1049604', 'Class_name'),
 ('__1049676', 'Class_name')}

In [8]:
instantiate("my_FSA", "State")

'__1054144'

# Inheritance

Another useful operation is to define inheritance between classes or associations.
For example, we can add the notion of an initial state, being a special case of the normal state.

In [9]:
model_add("formalisms/MyOwnFSA", "formalisms/SimpleClassDiagrams", """
    Class State {
        name = "State"
    }

    Class InitialState : State {
        name = "InitialState"
    }

    Association Transition (State, State) {
        name = "Transition"
    }
    """)

And indeed, this allows us to create an initial state, which is handled as both an instance of state and initial.

In [10]:
instantiate("my_FSA", "InitialState")
print("All initial element IDs: " + str(all_instances("my_FSA", "InitialState")))
print("All state element IDs: " + str(all_instances("my_FSA", "State")))

All initial element IDs: {'__1063123'}
All state element IDs: {'__1054144', '__1063123'}


# Attributes

On these classes and transitions, we want to define some attributes which instances can use.
To do that, however, we need to define attribute types.
The Modelverse does not predefine any attribute types at the modelling level (only physically), thereby giving the user full control over the supported types.

In [11]:
model_add("formalisms/MyOwnFSA", "formalisms/SimpleClassDiagrams", """
    include "primitives.alh"
    include "modelling.alh"
    include "object_operations.alh"

    SimpleAttribute String {
        name = "String"
    }

    ActionLanguage Action {}

    Class State {
        name = "State"
        name : String
    }

    Class InitialState : State {
        name = "InitialState"
    }

    Association Transition (State, State) {
        name = "Transition"
        trigger : String {}
        raise : String {}
        script : Action {}
    }
    """)

Now attributes can be instantiated on these instances.

In [12]:
new_state = instantiate("my_FSA", "State")
attr_assign("my_FSA", new_state, "name", "FirstState")
print(read_attrs("my_FSA", new_state))

{'name': 'FirstState'}


Note, however, that our model now no longer conforms: there are still some states that do not have any value for the name attribute.
Indeed, our metamodel has evolved, thereby invalidating the model.

In [13]:
print(verify("my_FSA", "formalisms/MyOwnFSA"))

Lower cardinality violation for outgoing edge of type State_name at NODE __1054144 (ID: 1054144)


If we now assign a value for every state that does not have a name, the model conforms again.

In [14]:
for counter, state in enumerate(all_instances("my_FSA", "State")):
    attr_assign("my_FSA", state, "name", "State_" + str(counter))
print(verify("my_FSA", "formalisms/MyOwnFSA"))

OK


# Attribute Constraints

As there are no types predefined, all constraints must be specified by the language engineer directly.
As such, it is now possible to assign whatever value to the attributes, as they are unconstrained.

In [15]:
attr_assign("my_FSA", new_state, "name", 123)
print(verify("my_FSA", "formalisms/MyOwnFSA"))

OK


We can now start constraining our custom string type as being a direct mapping to the physical type string, as defined in the MvS.
This is done by assigning a constraint function to the attribute.

In [16]:
model_add("formalisms/MyOwnFSA", "formalisms/SimpleClassDiagrams", """
    include "primitives.alh"
    include "modelling.alh"
    include "object_operations.alh"

    SimpleAttribute String {
        name = "String"
        constraint = $
            String function constraint(model : Element, name : String):
                if (is_physical_string(model["model"][name])):
                    return "OK"!
                else:
                    return "String has non-string value"!
            $
    }

    ActionLanguage Action {}

    Class State {
        name = "State"
        name : String
    }

    Class InitialState : State {
        name = "InitialState"
    }

    Association Transition (State, State) {
        name = "Transition"
        trigger : String {}
        raise : String {}
        script : Action {}
    }
    """)

This yields the expected result.

In [17]:
attr_assign("my_FSA", new_state, "name", 123)
print(verify("my_FSA", "formalisms/MyOwnFSA"))

String has non-string value


# Global Constraints

Similarly, global constraints can also be defined, which get access to the complete model.
These are special elements, similar to classes.
In this case, we check that there is at least one instance of the InitialState class.

In [18]:
model_add("formalisms/MyOwnFSA", "formalisms/SimpleClassDiagrams", """
    include "primitives.alh"
    include "modelling.alh"
    include "object_operations.alh"

    SimpleAttribute String {
        name = "String"
        constraint = $
            String function constraint(model : Element, name : String):
                if (is_physical_string(model["model"][name])):
                    return "OK"!
                else:
                    return "String has non-string value"!
            $
    }

    ActionLanguage Action {}

    Class State {
        name = "State"
        name : String
    }

    Class InitialState : State {
        name = "InitialState"
    }

    Association Transition (State, State) {
        name = "Transition"
        trigger : String {}
        raise : String {}
        script : Action {}
    }

    GlobalConstraint {
        constraint = $
            String function constraint(model : Element):
                Integer initials
                initials = set_len(allInstances(model, "InitialState"))
                if (initials == 0):
                    return "No initial state found"!
                elif (initials > 1):
                    return "Too many initial states defined"!
                else:
                    return "OK"!
            $
    }
    """)

# Local Constraint Helpers

Most constraints are related to the multiplicities of associations and classes.
For example, we want to make sure that there is exactly one instance of a specific class (e.g., InitialState).
Similarly, for an association we might want to define that there is at least one such.
The Modelverse provides various such attributes that can be set.
For example, to constrain the number of instances, use the *lower_cardinality* and *upper_cardinality* attributes.
For associations, there are additionally the *source_lower_cardinality*, *source_upper_cardinality*, *target_lower_cardinality*, and *target_upper_cardinality* attributes.

In [19]:
model_add("formalisms/MyOwnFSA", "formalisms/SimpleClassDiagrams", """
    include "primitives.alh"
    include "modelling.alh"
    include "object_operations.alh"

    SimpleAttribute String {
        name = "String"
        constraint = $
            String function constraint(model : Element, name : String):
                if (is_physical_string(model["model"][name])):
                    return "OK"!
                else:
                    return "String has non-string value"!
            $
    }

    ActionLanguage Action {}

    Class State {
        name = "State"
        name : String
    }

    Class InitialState : State {
        name = "InitialState"
        lower_cardinality = 1
        upper_cardinality = 1
    }

    Association Transition (State, State) {
        name = "Transition"
        trigger : String {}
        raise : String {}
        script : Action {}
    }
    """)

# Optional Attributes

Often, not all of the attributes are mandatory, and they can therefore be left empty.
During conformance checking, these attributes are then not enforced.
When reading out their value, however, the language engineer must take care that the value might be empty.

In [20]:
model_add("formalisms/MyOwnFSA", "formalisms/SimpleClassDiagrams", """
    include "primitives.alh"
    include "modelling.alh"
    include "object_operations.alh"

    SimpleAttribute String {
        name = "String"
        constraint = $
            String function constraint(model : Element, name : String):
                if (is_physical_string(model["model"][name])):
                    return "OK"!
                else:
                    return "String has non-string value"!
            $
    }

    ActionLanguage Action {}

    Class State {
        name = "State"
        name : String
    }

    Class InitialState : State {
        name = "InitialState"
        lower_cardinality = 1
        upper_cardinality = 1
    }

    Association Transition (State, State) {
        name = "Transition"
        trigger? : String {}
        raise? : String {}
        script? : Action {}
    }
    """)

# Incremental Construction

Alternatively, the metamodel can be created incrementally.

In [21]:
mm = "formalisms/MyOwnFSA2"

model_add(mm, "formalisms/SimpleClassDiagrams")

str_attr = instantiate(mm, "SimpleAttribute")
attr_assign(mm, str_attr, "name", "String")
attr_assign_code(mm, str_attr, "constraint", """
    include "primitives.alh"
    
    String function constraint(model : Element, name : String):
        if (is_physical_string(model["model"][name])):
            return "OK"!
        else:
            return "String has non-string value"!
    """)
al_attr = instantiate(mm, "ActionLanguage")

state = instantiate(mm, "Class")
attr_assign(mm, state, "name", "State")
define_attribute(mm, state, "name", str_attr)

initial = instantiate(mm, "Class")
attr_assign(mm, initial, "name", "InitialState")
instantiate(mm, "Inheritance", edge=(initial, state))
attr_assign(mm, initial, "lower_cardinality", 1)
attr_assign(mm, initial, "upper_cardinality", 1)

transition = instantiate(mm, "Association", edge=(state, state))
attr_assign(mm, transition, "name", "Transition")
define_attribute(mm, transition, "trigger", str_attr)
attribute_optional(mm, transition, "trigger", True)
define_attribute(mm, transition, "raise", str_attr)
attribute_optional(mm, transition, "raise", True)
define_attribute(mm, transition, "script", al_attr)
attribute_optional(mm, transition, "script", True)

# Semantics

While we have created the syntax of the new language, it should still be possible to define the semantics.
The Modelverse supports three main types of activity, each with their own ideal problem domain.

## Manual

The first type of activity is also the easiest to define, as it is a manual activity.
Many types of activity, or modifications of a model, have to be done manually as they augment information.
For example, refinement is a typical operation that requires a modeller to manually add information to the model.

For our own defined FSAs, assume that we want to add a *revise* activity, in which the modeller is prompted to modify the model.
While this does not give much information to the Modelverse, it is required, for example, to integrate manual activities in a process model.

In [22]:
transformation_add_MANUAL({"FSA": "formalisms/MyOwnFSA"}, {"FSA": "formalisms/MyOwnFSA"}, "formalisms/MyOwnFSA_activities/revise")

Now we can see it in action.
But as was mentioned, it will take manual operations, in our case through the use of a callback function.

In [23]:
def callback(model):
    state = instantiate(model, "FSA/State")
    attr_assign(model, state, "name", "new_state")
    
model_add("models/my_FSA", "formalisms/MyOwnFSA")

print("Before:")
print(element_list_nice("models/my_FSA"))

transformation_execute_MANUAL("formalisms/MyOwnFSA_activities/revise", {"FSA": "models/my_FSA"}, {"FSA": "models/my_FSA"}, callback)

print("After:")
print(element_list_nice("models/my_FSA"))

Before:
[]
After:
[{'__id': '__1278420', '__type': 'State', 'name': 'new_state'}]


## Action Language

Another typical execution scenario is for procedural operations to execute.
In the simplest case, this merely calls some action language code with the selected model as a parameter.
Note that this parameter will be a single model, consisting of the merged model and metamodel.

For our own defined FSAs, assume that we want to add a simple simulation algorithm.
Note the "return True" at the end, signifying that the operation was terminated OK and that changes can be propagated.

In [28]:
transformation_add_AL({"FSA": "formalisms/MyOwnFSA"}, {}, "formalisms/MyOwnFSA_activities/simulate", """
include "primitives.alh"
include "modelling.alh"
include "object_operations.alh"
include "conformance_scd.alh"
include "io.alh"
include "metamodels.alh"
include "mini_modify.alh"
include "library.alh"

Boolean function main(model : Element):
    String input_value
    Float start_time
    String current_state
    String old_state
    Element transitions
    String transition

    start_time = time()

    Element all_states
    String element_name
    all_states = allInstances(model, "FSA/State")
    while (set_len(all_states) > 0):
        element_name = set_pop(all_states)
        if (read_type(model, element_name) == "FSA/InitialState"):
            current_state = element_name
            old_state = element_name
            break!

    while (time() - start_time < 10.0):
        if (has_input()):
            input_value = list_read(string_split(input(), "\\n"), 0)
            log("Received input value: " + cast_string(input_value))
            if (input_value == "__EXIT__"):
                break!

            transitions = allOutgoingAssociationInstances(model, current_state, "FSA/Transition")
            while (set_len(transitions) > 0):
                transition = set_pop(transitions)
                log("Compare against " + cast_string(read_attribute(model, transition, "trigger")))
                if (cast_string(read_attribute(model, transition, "trigger")) == input_value):
                    if (element_neq(read_attribute(model, transition, "raise"), read_root())):
                        log(cast_value(time() - start_time) + " output " + cast_string(read_attribute(model, transition, "raise")))
                        output(cast_value(time() - start_time) + " output " + cast_string(read_attribute(model, transition, "raise")))
                    if (element_neq(read_attribute(model, transition, "script"), read_root())):
                        Element func
                        func = get_func_AL_model(import_node(read_attribute(model, transition, "script")))
                        func()
                    current_state = readAssociationDestination(model, transition)
                    break!

        log(cast_value(time() - start_time) + " " + cast_string(read_attribute(model, current_state, "name")))
        output(cast_value(time() - start_time) + " " + cast_string(read_attribute(model, current_state, "name")))
        sleep(0.2)
    return True!
    """)

Now we can see it in action.
For now, we just rely on the end time of the simulation (and no inputs happen), but otherwise we would have to couple it to an SCCD model.

In [25]:
model_add("models/my_FSA", "formalisms/MyOwnFSA", """
    InitialState init{
        name = "initial"
    }
    State s1{
        name = "S1"
    }
    State s2{
        name = "S2"
    }
    Transition (init, s1) {
        trigger = "B"
        raise = "C"
    }
    Transition (s1, s2) {
        trigger = "A"
        raise = "D"
    }
    """)
transformation_execute_AL("formalisms/MyOwnFSA_activities/simulate", {"FSA": "models/my_FSA"}, {})

True

## Model Transformation

Finally, it is possible to define a model transformation.
This requires RAMification and such, but this is all done transparently by the Modelverse.
Defining a model transformation is therefore identical to defining an Action Language activity, except that now we pass a model of transformations and rules, instead of passing an action language fragment.

For our defined FSAs, assume that we want to add a simple optimization transformation, removing all states that have no incoming transition.

In [26]:
transformation_add_MT({"FSA": "formalisms/MyOwnFSA"}, {"FSA": "formalisms/MyOwnFSA"}, "formalisms/MyOwnFSA_activities/optimize", """
include "primitives.alh"
include "modelling.alh"
include "object_operations.alh"

Composite schedule {
    {Contains} Success success {}
    {Contains} ForAll optimize {
        NAC { 
            Pre_FSA/State nac_s_1 {
                label = "0"
            }
            Pre_FSA/State nac_s_2 {
                label = "1"
            }
            Pre_FSA/Transition nac_s_3 (nac_s_2, nac_s_1) {
                label = "2"
            }
        }
        LHS {
            Pre_FSA/State pre_s_1 {
                label = "0"
                constraint = $
                    Boolean function not_initial(model : Element, name : String):
                        if (read_type(model, name) == "FSA/InitialState"):
                            return False!
                        else:
                            return True!
                $
            }
        }
        RHS {
        }
    }    
}

Initial (schedule, optimize) {}
OnSuccess (optimize, optimize) {}
OnFailure (optimize, success) {}
    """)

Now we can see it in action.

In [27]:
model_add("models/my_FSA", "formalisms/MyOwnFSA", """
    InitialState a {
        name = "A"
    }
    State b {
        name = "B"
    }
    State c {
        name = "C"
    }
    Transition (a, b) {}
""")

print("Before:")
print(all_instances("models/my_FSA", "State"))

transformation_execute_MT("formalisms/MyOwnFSA_activities/optimize", {"FSA": "models/my_FSA"}, {"FSA": "models/my_FSA"})

print("After:")
print(all_instances("models/my_FSA", "State"))

Before:
{'a', 'c', 'b'}
After:
{'a', 'b'}


## Traceability Links

It is often useful to have multiple metamodels that integrate with one another.
For example, when defining denotational semantics, we might want to create traceability links between both formalisms.
As in the Modelverse everything must be explicitly modelled, these links should also follow the usual modelling conventions.
That is, the links must have a type defined.
For that purpose, the Modelverse create a *merged* metamodel on which the activities actually occur.
It is possible to define a callback in each of the *transformation_add_* operations, which are then able to alter this merged metamodel.
Such alterations can, for example, include adding a traceability link between elements from different origining metamodels.
For more details, refer to the documentation.